# Structural Alignment and Evolutionary Analysis of Fusexin Proteins

Welcome! In this notebook, you will explore the structure and evolution of fusexin proteins using hands-on bioinformatics tools and methods. The protein structures are provided in the `example_fusexins` directory and are based on [this Nature Communications article](https://www.nature.com/articles/s41467-022-31564-1).

## Objectives
- **Visualize protein structures:** Explore and inspect fusexin protein 3D structures.
- **Structural alignment:** Apply multiple methods to align and compare protein structures.
- **Sequence analysis:** Perform sequence alignments and build phylogenetic trees.
- **Advanced analysis:** Use the foldtree method for deeper structural insights.

## Workflow Overview
1. Visualize fusexin protein structures
2. Align and compare structures
3. Perform sequence alignment and phylogenetic analysis
4. Apply foldtree for advanced structural analysis

---

Let's get started!

In [10]:
cd projects/Structural_evo_tutorial/Structural_evo_tutorial/

/home/dmoi/projects/Structural_evo_tutorial/Structural_evo_tutorial


In [12]:
#let's load the dataset

import glob
fusexins = glob.glob( './fsx1/*.pdb')
print( len(fusexins), 'fusexins found')
print( fusexins[0:5] , '...' )

16 fusexins found
['./fsx1/WP_049937247_Hnatans.pdb', './fsx1/5mf1_C_reinhardtii.pdb', './fsx1/1OAN_Dengue.pdb', './fsx1/7P4L_metageno_halo.pdb', './fsx1/WP_058826362_Haloferax.pdb'] ...


### Structural Organization of Class II Fusion Proteins

Class II fusion proteins / fusexins are typically organized into three distinct domains:

- **Domain I:** This central domain is β-rich and stabilized by multiple disulfide bonds. It forms the core scaffold of the protein and often contains the hydrophobic "fusion loop" at its tip. The fusion loop is critical for initiating membrane fusion, as it inserts into the target membrane to promote the merging of lipid bilayers.

- **Domain II:** Like Domain I, Domain II is also β-rich and stabilized by disulfide bonds. It is usually elongated and forms an extended structure that helps position the fusion loop for membrane engagement.

- **Domain III:** This domain adopts a classic immunoglobulin (Ig)-like fold. It is more globular and is thought to contribute to the structural stability and proper folding of the fusion protein.

The spatial arrangement of these domains allows the fusion loop in Domain I to be optimally positioned for membrane insertion, while Domains II and III provide structural support and flexibility necessary for the large conformational changes that drive membrane fusion.

In [ ]:
import py3Dmol
#let's visualize the first one with py3Dmol and use domain specific colors

def visualize_structure_with_coloring(pdb_path, color_ranges, chain_id='A', alpha=0.7):
	"""
	Visualize a protein structure with colored ribbon and opaque grey surface using py3Dmol.

	Args:
		pdb_path (str): Path to the PDB file.
		color_ranges (list of tuples): List of (start_res, end_res, color) for coloring.
		chain_id (str): Chain ID to visualize (default: 'A').
		alpha (float): Opacity for the surface (0.0 to 1.0).
	"""
	with open(pdb_path) as f:
		pdb_data = f.read()

	view = py3Dmol.view(width=600, height=400)
	view.addModel(pdb_data, 'pdb')
	# Add opaque grey surface
	view.addSurface(py3Dmol.VDW, {'opacity': alpha, 'color': 'grey', 'sele': {'chain': chain_id}})
	# Add colored cartoon for specified ranges
	for start, end, color in color_ranges:
		selection = {'chain': chain_id, 'resi': list(range(start, end + 1))}
		view.addCartoon({'sele': selection, 'color': color})
	# Show the rest of the chain in light grey
	view.addCartoon({'sele': {'chain': chain_id}, 'color': 'lightgrey'})
	view.zoomTo({'chain': chain_id})
	return view



In [ ]:
import py3Dmol

def visualize_structure_with_coloring(pdb_path, color_ranges, chain_id='A', alpha=0.7):
	"""
	Visualize a protein structure with colored ribbon and opaque grey surface using py3Dmol.

	Args:
		pdb_path (str): Path to the PDB file.
		color_ranges (list of tuples): List of (start_res, end_res, color) for coloring.
		chain_id (str): Chain ID to visualize (default: 'A').
		alpha (float): Opacity for the surface (0.0 to 1.0).
	"""
	with open(pdb_path) as f:
		pdb_data = f.read()

	view = py3Dmol.view(width=600, height=400)
	view.addModel(pdb_data, 'pdb')
	# Add opaque grey surface
	view.addSurface(py3Dmol.VDW, {'opacity': alpha, 'color': 'grey', 'sele': {'chain': chain_id}})
	# Add colored cartoon for specified ranges
	for start, end, color in color_ranges:
		selection = {'chain': chain_id, 'resi': list(range(start, end + 1))}
		view.addCartoon({'sele': selection, 'color': color})
	# Show the rest of the chain in light grey
	view.addCartoon({'sele': {'chain': chain_id}, 'color': 'lightgrey'})
	view.zoomTo({'chain': chain_id})
	return view

In [ ]:
from Bio.PDB import Superimposer, PDBParser
from Bio.PDB import PDBIO
import tempfile
import py3Dmol

def rigid_body_align(structure_path1, structure_path2, chain_id1='A', chain_id2='A'):
	"""
	Align two protein structures using rigid body superposition.

	Returns:
		rmsd (float): Root mean square deviation after alignment.
		super_imposer (Superimposer): Biopython Superimposer object.
		structure1, structure2: Biopython Structure objects (structure2 is superposed).
		view (py3Dmol.view): py3Dmol view showing the superposed structures.
	"""
	parser = PDBParser(QUIET=True)
	structure1 = parser.get_structure('struct1', structure_path1)
	structure2 = parser.get_structure('struct2', structure_path2)

	atoms1 = [atom for atom in structure1[0].get_atoms() if atom.get_id() == 'CA']
	atoms2 = [atom for atom in structure2[0].get_atoms() if atom.get_id() == 'CA']

	min_len = min(len(atoms1), len(atoms2))
	atoms1 = atoms1[:min_len]
	atoms2 = atoms2[:min_len]

	sup = Superimposer()
	sup.set_atoms(atoms1, atoms2)
	sup.apply(structure2.get_atoms())

	# Save structures to temp files for visualization
	io = PDBIO()
	# structure1
	tmp1 = tempfile.NamedTemporaryFile(delete=False, suffix='.pdb')
	io.set_structure(structure1)
	io.save(tmp1.name)
	# structure2 (already superposed)
	tmp2 = tempfile.NamedTemporaryFile(delete=False, suffix='.pdb')
	io.set_structure(structure2)
	io.save(tmp2.name)

	# Visualize with py3Dmol
	with open(tmp1.name) as f1, open(tmp2.name) as f2:
		pdb1 = f1.read()
		pdb2 = f2.read()
	view = py3Dmol.view(width=600, height=400)
	view.addModel(pdb1, 'pdb')
	view.setStyle({'model': 0}, {'cartoon': {'color': 'spectrum'}})
	view.addModel(pdb2, 'pdb')
	view.setStyle({'model': 1}, {'cartoon': {'color': 'magenta'}})
	view.zoomTo()
	return sup.rms, sup, structure1, structure2, view


In [21]:
#let's try some structure pairs
import itertools
import random
combos = [ ( i, j ) for i, j in itertools.combinations(range(len(fusexins)), 2) ]
sample = random.sample(combos, 5)
for i, j in sample:
	print( i, j, fusexins[i], fusexins[j] )
	rms, sup, structure1, structure2, view = rigid_body_align(fusexins[i], fusexins[j])
	view.show()
	print( 'RMSD:', rms)
# The above code will align the first two structures in the list and print the RMSD.
# lets also save the aligned structures
sup.apply(structure2.get_atoms())
# Save the aligned structure


3 6 ./fsx1/7P4L_metageno_halo.pdb ./fsx1/4OJC_C_elegans.pdb


3Dmol.js failed to load for some reason. Please check your browser console for error messages.

RMSD: 32.23147016519277
5 12 ./fsx1/WP_007110832_Naltunense.pdb ./fsx1/6EGU_Rift_valley_fever_virus.pdb


3Dmol.js failed to load for some reason. Please check your browser console for error messages.

RMSD: 17.05064296162326
5 9 ./fsx1/WP_007110832_Naltunense.pdb ./fsx1/3n43_Chikungunya_virus.pdb


...

RMSD: 35.31038538574161
0 2 ./fsx1/WP_049937247_Hnatans.pdb ./fsx1/1OAN_Dengue.pdb


3Dmol.js failed to load for some reason. Please check your browser console for error messages.

RMSD: 35.155733894491654
11 12 ./fsx1/5OW3_A_thaliana.pdb ./fsx1/6EGU_Rift_valley_fever_virus.pdb


3Dmol.js failed to load for some reason. Please check your browser console for error messages.

RMSD: 20.265834830658463


## Structural Homology Despite Conformational Diversity

The structural alignments above demonstrate that these fusexin proteins are homologous, sharing a common evolutionary origin. However, their overall conformations can differ significantly. In some cases, large domain movements or flexible regions may cause parts of the structures to be misaligned, resulting in higher RMSD values even when the underlying homology is clear.

## Interpreting RMSD in Structural Comparisons

It is important to recognize that high RMSD values do not necessarily indicate a lack of evolutionary relationship. Instead, they may reflect conformational flexibility or domain rearrangements that occur independently of evolutionary divergence. Careful interpretation of RMSD in the context of protein evolution is therefore essential.

## Transition to Sequence-Based Phylogeny

Once structural homology has been established, the next logical step is to investigate the evolutionary history of these proteins at the sequence level. In the following sections, we will construct a sequence-based phylogeny to further explore the evolutionary relationships among these fusexin proteins.

### Interpreting RMSD in the Context of Protein Evolution

While RMSD (Root Mean Square Deviation) is a useful metric for quantifying structural differences between protein conformations, it is important to recognize its limitations in evolutionary analysis. RMSD is highly sensitive to **conformational changes**—such as domain movements or flexible loop rearrangements—that may occur due to thermal fluctuations or experimental conditions. These changes can result in large RMSD values even when the overall fold and evolutionary relationship remain conserved.

In contrast, **evolutionary divergence** typically involves small, local, and iterative changes at the level of individual residues. RMSD does not specifically capture these subtle, residue-level substitutions and may therefore **overestimate evolutionary distance** when comparing structures with different conformational states. For evolutionary studies, it is often more informative to use metrics or methods that account for local structural conservation and sequence changes, rather than relying solely on global RMSD.

In [ ]:
import subprocess
import tempfile


# here we set up some functions to run IQ-TREE and MAFFT
# this is a typical workflow for phylogenetic analysis

def run_iqtree_with_lg_invariant(fasta_path, iqtree_path='iqtree2', threads=2):
	"""
	Run IQ-TREE on a FASTA MSA using the LG model with invariant sites.

	Args:
		fasta_path (str): Path to the input FASTA MSA file.
		iqtree_path (str): Path to the IQ-TREE executable (default: 'iqtree2').
		threads (int): Number of CPU threads to use (default: 2).

	Returns:
		result (subprocess.CompletedProcess): The result of the IQ-TREE run.
	"""
	cmd = [
		iqtree_path,
		'-s', fasta_path,
		'-m', 'LG+I',
		'-nt', str(threads)
	]
	result = subprocess.run(cmd, capture_output=True, text=True)
	return result

def run_mafft_on_sequences(sequences, mafft_path='mafft'):
	"""
	Run MAFFT on a list of sequences.

	Args:
		sequences (list of str): List of sequences in FASTA format (with headers).
		mafft_path (str): Path to the MAFFT executable (default: 'mafft').

	Returns:
		str: Aligned sequences in FASTA format.
	"""

	with tempfile.NamedTemporaryFile(mode='w+', delete=False) as fasta_file:
		fasta_file.write('\n'.join(sequences))
		fasta_file.flush()
		cmd = [mafft_path, '--auto', fasta_file.name]
		result = subprocess.run(cmd, capture_output=True, text=True)
	return result.stdout

def root_newick_with_mad(newick_str, mad_path='MAD', tmp_prefix='madtmp'):
	"""
	Root a Newick tree using the MAD (Minimal Ancestor Deviation) method.

	Args:
		newick_str (str): Unrooted tree in Newick format.
		mad_path (str): Path to the MAD executable (default: 'MAD').
		tmp_prefix (str): Prefix for temporary files.

	Returns:
		str: Rooted Newick tree as a string.
	"""
	with tempfile.NamedTemporaryFile(mode='w+', suffix='.nwk', prefix=tmp_prefix, delete=False) as tree_file:
		tree_file.write(newick_str)
		tree_file.flush()
		tree_file_path = tree_file.name

	# MAD outputs a rooted tree to <input>.rooted
	rooted_tree_path = tree_file_path + '.rooted'
	cmd = [mad_path, tree_file_path]
	result = subprocess.run(cmd, capture_output=True, text=True)
	if result.returncode != 0:
		raise RuntimeError(f"MAD failed: {result.stderr}")

	with open(rooted_tree_path, 'r') as f:
		rooted_newick = f.read().strip()
	return rooted_newick

## The LG Evolutionary Model and Invariant Sites in Phylogenetic Analysis

When inferring phylogenetic trees from protein sequences, it is crucial to use an evolutionary model that accurately reflects the patterns of amino acid substitutions. In this analysis, we use the **LG model** (Le and Gascuel, 2008), a widely adopted empirical substitution matrix derived from a large set of curated protein alignments. The LG model is particularly suitable for diverse protein families, as it captures the varying rates at which different amino acids are substituted over evolutionary time.

### Invariant Sites (+I)

To further improve the fit of the model to our data, we include a parameter for **invariant sites** (`+I`). This accounts for the fact that some positions in the protein alignment are highly conserved and do not change across the sequences. By modeling these sites as invariant, we avoid overestimating the evolutionary rate and obtain more accurate branch lengths and tree topologies.

### Application in IQ-TREE

We use **IQ-TREE** to estimate the maximum likelihood phylogeny from a multiple sequence alignment (MSA) in FASTA format. The command specifies the LG model with invariant sites (`-m LG+I`). This is especially important for our dataset, as the fusexin protein family is highly divergent at the sequence level. Using an appropriate model helps to mitigate the challenges posed by high sequence divergence and leads to more reliable evolutionary inferences.

### Minimal Ancestor Deviation (MAD) Rooting

**Minimal Ancestor Deviation (MAD)** is a method for rooting phylogenetic trees that does not require an explicit outgroup. Instead, MAD identifies the root position that minimizes the deviation from a molecular clock across all pairs of taxa in the tree. This approach assumes that, on average, evolutionary rates are similar along different lineages—a reasonable assumption for both sequence-based and structure-based phylogenies.

By minimizing the ancestor deviation, MAD finds the root that best balances the tree, making it especially useful when outgroup selection is ambiguous or when comparing highly divergent proteins. This method is robust and broadly applicable, providing a consistent rooting strategy for both sequence and structural evolutionary analyses.

In [ ]:
from Bio.PDB import PDBParser, PPBuilder
from Bio.SeqRecord import SeqRecord
from Bio.Seq import Seq
from Bio import SeqIO

#now that we have our functions let's run them
#first we need to create a fasta file with the sequences

# Extract sequences from all fusexin PDB files
parser = PDBParser(QUIET=True)
ppb = PPBuilder()
seq_records = []

for idx, pdb_path in enumerate(fusexins):
	structure = parser.get_structure(f"fusexin_{idx}", pdb_path)
	# Get the first chain (usually 'A')
	for model in structure:
		for chain in model:
			# Build polypeptides and extract sequence
			polypeptides = ppb.build_peptides(chain)
			if polypeptides:
				seq = polypeptides[0].get_sequence()
				name = pdb_path.split('/')[-1].split('.')[0]
				record = SeqRecord(Seq(str(seq)), id=name )
				seq_records.append(record)
			break  # Only use the first chain
		break  # Only use the first model

# Write to FASTA file
fasta_path = "fusexins_sequences.fasta"
SeqIO.write(seq_records, fasta_path, "fasta")
print(f"FASTA file written to {fasta_path}")

FASTA file written to fusexins_sequences.fasta


In [3]:
from Bio import AlignIO

import matplotlib.pyplot as plt

def plot_identity_and_gaps(alignment_path, format='fasta'):
	"""
	Plot percent identity and percent gaps for each column in a sequence alignment.

	Args:
		alignment_path (str): Path to the alignment file.
		format (str): Alignment file format (default: 'fasta').
	"""
	alignment = AlignIO.read(alignment_path, format)
	n_seqs = len(alignment)
	aln_len = alignment.get_alignment_length()
	percent_identity = []
	percent_gaps = []

	for i in range(aln_len):
		column = alignment[:, i]
		gap_count = column.count('-')
		most_common = max(set(column.replace('-', '')), key=column.count, default='-')
		identity_count = column.count(most_common)
		percent_identity.append(100 * identity_count / n_seqs)
		percent_gaps.append(100 * gap_count / n_seqs)

	plt.figure(figsize=(12, 4))
	plt.plot(percent_identity, label='Percent Identity')
	plt.plot(percent_gaps, label='Percent Gaps')
	plt.xlabel('Alignment Column')
	plt.ylabel('Percent (%)')
	plt.title('Percent Identity and Gaps per Alignment Column')
	plt.legend()
	plt.tight_layout()
	plt.show()

In [ ]:
import numpy as np
import pandas as pd
from Bio import AlignIO

def hamming_distance(seq1, seq2):
	"""Compute Hamming distance between two aligned sequences (counting only non-gap positions)."""
	assert len(seq1) == len(seq2)
	return sum((a != b) and (a != '-' and b != '-') for a, b in zip(seq1, seq2))

def hamming_distance_matrix(alignment_path, format='fasta'):
	"""
	Compute the Hamming distance matrix for all sequences in an alignment file.
	Returns a pandas DataFrame with sequence IDs as row/column labels.
	"""
	alignment = AlignIO.read(alignment_path, format)
	ids = [record.id for record in alignment]
	n = len(alignment)
	matrix = np.zeros((n, n), dtype=int)
	for i in range(n):
		for j in range(n):
			if i <= j:
				dist = hamming_distance(str(alignment[i].seq), str(alignment[j].seq))
				matrix[i, j] = dist
				matrix[j, i] = dist
	df = pd.DataFrame(matrix, index=ids, columns=ids)
	return df

hamming_df = hamming_distance_matrix(aln_path)
print(hamming_df)

### Exploring Sequence Conservation and Alignment Approaches

Now that you have generated a multiple sequence alignment (MSA), you can inspect it visually using tools like **Jalview** or **AliView**. These tools allow you to:

- Identify **conserved positions** across all fusexin homologs.
- Highlight regions with high sequence variability or gaps.
- Examine whether conserved residues correspond to known functional motifs or structural features (e.g., the fusion loop).

#### Questions for Exploration

- **Are there any highly conserved positions in the alignment?**  
	Do these conserved residues cluster in specific domains or functional regions of the protein?

- **How do the conserved sequence positions compare to structurally conserved regions?**  
	Are the residues that are structurally aligned by rigid body superposition also conserved at the sequence level?

- **What challenges arise when aligning highly divergent homologs?**  
	When sequence identity is low, do sequence-based alignments still correctly align functionally equivalent residues, or do they become ambiguous?

- **How does structural alignment (e.g., rigid body superposition) differ from sequence alignment in this context?**  
	Can structural methods align homologous residues that are no longer detectable by sequence similarity alone? What are the limitations of each approach?

#### Reflection

When homologs are highly divergent, **sequence-based alignments** may fail to correctly align functionally equivalent or structurally important residues, especially in regions with low conservation. In contrast, **structure-based alignments** can often reveal deeper evolutionary relationships by aligning residues based on their 3D positions, even when sequence similarity is minimal. Let's press on and make the tree!

In [ ]:
# We can see theyre all homologous but conformationally different

### Foldseek Structural Alphabet: Local Structural Characters for Evolutionary Analysis

Foldseek introduces a **structural alphabet** that encodes local protein structure using a sliding window of 6 amino acids. Each window is mapped to a discrete "structural character" based on the local backbone geometry. Because these characters are **locally defined**, they are largely invariant to global conformational changes, such as domain movements or flexible loops.

This local encoding enables **rapid structural comparison** by transforming the 3D alignment problem into a much faster string alignment task. Importantly, the local nature of the structural alphabet makes Foldseek-based comparisons robust to conformational variability, allowing for more accurate estimation of **evolutionary distances** between homologous proteins, even when their overall shapes differ due to flexibility or experimental conditions.

Our study ([Moi et al., 2023](https://www.biorxiv.org/content/10.1101/2023.09.19.558401v2)) demonstrated that using Foldseek-derived structural distances provides improved accuracy for reconstructing evolutionary relationships, especially for highly divergent protein families.


In [ ]:
from fold_tree.src.foldseek2tree import *

In [ ]:
# let's run foldtree. It outputs paiwise comparisons 

In [ ]:
#let's compare these distances to the hamming distances we got from the sequences



## Why Does Structural Geometry Remain Constrained While Sequence Divergence Saturates ?

Why is it that, even as protein sequences diverge to the point where Hamming distances saturate, the overall structural geometry of proteins does not diverge beyond certain limits under functional or biophysical constraints? What does this tell us about the relationship between the vastness of sequence space and the relatively limited number of protein folds observed in nature? Does the persistence of structural similarity, despite extreme sequence divergence, help explain why so many different sequences can map onto a much smaller set of stable, functional folds ?



In [ ]:
import toytree

#lets visualize the tree and compare the maximum likelihood tree with toytree
def show_two_trees_with_fixed_order(tree1_newick, tree2_newick):
	"""
	Visualize two trees side by side in toytree, with leaf order defined by the first tree,
	using coalescent ('c') style.

	Args:
		tree1_newick (str): Newick string for the reference tree (defines leaf order).
		tree2_newick (str): Newick string for the second tree to compare.
	"""
	# Load trees
	t1 = toytree.tree(tree1_newick)
	t2 = toytree.tree(tree2_newick)
	# Get leaf order from first tree
	leaf_order = [leaf.treenode.name for leaf in t1.treenode.iter_leaves()]
	# Draw both trees with the same leaf order and coalescent style
	canvas = toytree.Canvas(width=800, height=400)
	canvas.add_tree(
		t1, layout="c", leaf_order=leaf_order, node_labels=False,
		edge_colors="steelblue", title="Reference Tree"
	)
	canvas.add_tree(
		t2, layout="c", leaf_order=leaf_order, node_labels=False,
		edge_colors="tomato", xpos=400, title="Comparison Tree"
	)
	display(canvas)

### Reflection: Parsimony and Structural Phylogeny

Consider the two phylogenetic trees you have generated—one based on sequence data (maximum likelihood) and the other on structural features (Foldseek/foldtree). 

- **Which approach do you think is more parsimonious in explaining the evolutionary relationships among these proteins?**
- **How does the structural phylogeny compare to the sequence-based tree, and what might this tell us about the evolutionary trajectory of the fusexin family?**

Reflect on how local structural conservation versus sequence similarity might influence your interpretation of protein evolution in this context.

# that's it for the introduction! Let's move on to another example that's a bit more complex.